In [2]:
# Importing libraries
import numpy as np
import pandas as pd
import pydub

from IPython.display import Audio
from keras.layers import Dense, LSTM, LeakyReLU
from keras.models import Sequential, load_model
from scipy.io.wavfile import read, write

C:\Users\HakiM\AppData\Local\Programs\Python\Python36\lib\site-packages\pydub\utils.py:170: RuntimeWarning: Couldn't find ffmpeg or avconv - defaulting to ffmpeg, but may not work
  warn("Couldn't find ffmpeg or avconv - defaulting to ffmpeg, but may not work", RuntimeWarning)


In [3]:
# Loading the wav files
music = ['','']
rate, music[0] = read('../dataset/wavLITE/train/true/Astral.wav')
rate, music[1] = read('../dataset/wavLITE/train/true/Bad Intentions.wav')

test_music = ['','']
rate, test_music[0] = read('../dataset/wavLITE/train/true/Harder.wav')
rate, test_music[1] = read('../dataset/wavLITE/train/true/Infinity Space.wav')

In [4]:
# Taking only some part of the songs and converting to a dataframe
music[0] = pd.DataFrame(music[0][0:400000, :])
music[1] = pd.DataFrame(music[1][0:400000, :])
test_music[0] = pd.DataFrame(test_music[0][0:400000, :])
test_music[1] = pd.DataFrame(test_music[1][0:400000, :])

In [4]:
# Function to create train data by shifting the music data 
def create_train_dataset(dataframe, look_back):
    x, y = [],[]
    for i in range(len(dataframe)-look_back-1):
        x.append(dataframe.iloc[i : i + look_back].values)
        y.append(dataframe.iloc[i + look_back])
    return np.array(x), np.array(y)

In [5]:
type(music)

list

In [72]:
x, y = create_train_dataset(pd.concat(music, axis=0), look_back=3)

In [82]:
# Function to create train data by shifting the music data
def create_test_data(dataframe, look_back):
    x = []
    for i in range(len(dataframe)-look_back-1):
        x.append(dataframe.iloc[i : i + look_back].values)
    return np.array(x)

In [83]:
test = create_test_data(test_music, 3)

In [74]:
x = x.reshape((-1, 1, 3))
y = y.reshape((-1,))

In [75]:
rnn1 = Sequential()
rnn1.add(LSTM(units=100, activation='linear', input_shape=(None, 3)))
rnn1.add(LeakyReLU())
rnn1.add(Dense(units=50, activation='linear'))
rnn1.add(LeakyReLU())
rnn1.add(Dense(units=25, activation='linear'))
rnn1.add(LeakyReLU())
rnn1.add(Dense(units=12, activation='linear'))
rnn1.add(LeakyReLU())
rnn1.add(Dense(units=1, activation='linear'))
rnn1.add(LeakyReLU())

rnn1.compile(optimizer='adam', loss='mean_squared_error')
rnn1.fit(x, y, epochs=20, batch_size=100)

Epoch 1/20
16000/16000 [==============================] - 40s 2ms/step - loss: 1118496.1779
Epoch 2/20
16000/16000 [==============================] - 39s 2ms/step - loss: 343523.7898
Epoch 3/20
16000/16000 [==============================] - 39s 2ms/step - loss: 331818.7806
Epoch 4/20
16000/16000 [==============================] - 38s 2ms/step - loss: 329644.9350
Epoch 5/20
16000/16000 [==============================] - 36s 2ms/step - loss: 324586.1037
Epoch 6/20
16000/16000 [==============================] - 38s 2ms/step - loss: 324308.8079
Epoch 7/20
16000/16000 [==============================] - 37s 2ms/step - loss: 326719.1201
Epoch 8/20
16000/16000 [==============================] - 39s 2ms/step - loss: 325166.1952
Epoch 9/20
16000/16000 [==============================] - 37s 2ms/step - loss: 325008.4740
Epoch 10/20
16000/16000 [==============================] - 38s 2ms/step - loss: 319556.1254
Epoch 11/20
16000/16000 [==============================] - 37s 2ms/step - loss: 324172.6

In [76]:
# saving LSTM model
rnn1.save('rnn1.h5')

In [77]:
# loading the saved model
rnn1 = load_model('rnn1.h5')

In [132]:
empty_x = np.zeros(music[0].shape, dtype='int')
empty_x

array([[0, 0],
       [0, 0],
       [0, 0],
       ...,
       [0, 0],
       [0, 0],
       [0, 0]])

In [141]:
music[0].shape

(400000, 2)

In [143]:
# making predictions for channel 1 and channel 2
pred_rnn = rnn1.predict(empty_x)

ValueError: in user code:

    C:\Users\HakiM\AppData\Local\Programs\Python\Python36\lib\site-packages\tensorflow\python\keras\engine\training.py:1478 predict_function  *
        return step_function(self, iterator)
    C:\Users\HakiM\AppData\Local\Programs\Python\Python36\lib\site-packages\tensorflow\python\keras\engine\training.py:1468 step_function  **
        outputs = model.distribute_strategy.run(run_step, args=(data,))
    C:\Users\HakiM\AppData\Local\Programs\Python\Python36\lib\site-packages\tensorflow\python\distribute\distribute_lib.py:1259 run
        return self._extended.call_for_each_replica(fn, args=args, kwargs=kwargs)
    C:\Users\HakiM\AppData\Local\Programs\Python\Python36\lib\site-packages\tensorflow\python\distribute\distribute_lib.py:2730 call_for_each_replica
        return self._call_for_each_replica(fn, args, kwargs)
    C:\Users\HakiM\AppData\Local\Programs\Python\Python36\lib\site-packages\tensorflow\python\distribute\distribute_lib.py:3417 _call_for_each_re

In [144]:
print(pred_rnn.reshape(799996, 2))

[[-13.472188 -13.472188]
 [-13.472188 -13.472188]
 [-13.472188 -13.472188]
 ...
 [-13.472188 -13.472188]
 [-13.472188 -13.472188]
 [-13.472188 -13.472188]]


In [142]:
# Saving the LSTM predicitons in wav format
write('pred_rnn.wav', 44100, pd.DataFrame(pred_rnn.reshape(799996, 2).astype('int16')).values)

In [108]:
Audio("pred_rnn.wav")